## Loading and plotting data

In [1]:
import pandas as pd
from urllib.request import urlopen
import json
import plotly.graph_objects as go

geo_url = "https://www.ogd.stadt-zuerich.ch/wfs/geoportal/Oeffentlich_zugaengliche_Parkhaeuser?service=WFS&version=1.1.0&request=GetFeature&outputFormat=GeoJSON&typename=poi_parkhaus_view"

geo_url = "https://www.ogd.stadt-zuerich.ch/wfs/geoportal/Oeffentlich_zugaengliche_Strassenparkplaetze_OGD?service=WFS&version=1.1.0&request=GetFeature&outputFormat=GeoJSON&typename=view_pp_ogd"

with urlopen(geo_url) as response:
    geo_data = json.load(response)

df = pd.json_normalize(geo_data, "features")

df["lon"] = df["geometry.coordinates"].apply(lambda row: row[0])
df["lat"] = df["geometry.coordinates"].apply(lambda row: row[1])

fig = go.Figure(go.Scattermapbox(lat=df["lat"], lon=df["lon"], mode="markers"))

fig.update_layout(
    mapbox_style="stamen-toner",
    mapbox_zoom=11,
    mapbox_center={"lon": 8.540327377790328, "lat": 47.37792336422763},
    height=600,
    width=900,
)

fig.show()

## Loading traffic data

In [2]:
from functools import reduce

years = list(range(2022, 2023))

base_url = (
    lambda year: f"https://data.stadt-zuerich.ch/dataset/sid_dav_verkehrszaehlung_miv_od2031/download/sid_dav_verkehrszaehlung_miv_OD2031_{year}.csv"
)


def load_data(year):
    df = pd.read_csv(base_url(year))
    df = df.rename(str.lower, axis="columns")
    return df


dfs = [load_data(year) for year in years]

/tmp/ipykernel_48109/556385080.py:11: DtypeWarning:

Columns (5,14) have mixed types. Specify dtype option on import or set low_memory=False.



In [39]:
df_traffic = reduce(lambda x, y: pd.concat([x, y]), dfs)
df_traffic = df_traffic.dropna()
df_traffic = df_traffic.groupby("zsname").agg({"ekoord": "mean", "nkoord": "mean", "anzfahrzeuge": "sum"}).reset_index()

In [40]:
import geopandas as gpd
import shapely
from shapely import wkt, ops
import numpy as np
from scipy.spatial import Voronoi
import plotly.express as px

min_e, max_e = df_traffic["ekoord"].min(), df_traffic["ekoord"].max()
min_n, max_n = df_traffic["nkoord"].min(), df_traffic["nkoord"].max()

poly_string = f"Polygon (({min_e} {min_n}, {min_e} {max_n}, {max_e} {max_n}, {max_e} {min_n}, {min_e} {min_n}))"

poly = wkt.loads(poly_string)
bound = poly.buffer(2000).envelope.boundary

b_points = [
    bound.interpolate(distance=d)
    for d in range(0, np.ceil(bound.length).astype(int), 10000000)
]
b_coords = np.array([[p.x, p.y] for p in b_points])

df_mean = df_traffic#.groupby("zsname")[["ekoord", "nkoord"]].mean().reset_index()

coords = np.transpose([df_mean["ekoord"], df_mean["nkoord"]])

all_coords = np.concatenate((b_coords, coords))

vor = Voronoi(points=all_coords)

lines = [
    shapely.geometry.LineString(vor.vertices[line])
    for line in vor.ridge_vertices
    if -1 not in line
]

reg_polys = ops.polygonize(lines)

geo_df = gpd.GeoDataFrame(geometry=gpd.GeoSeries(reg_polys), crs="epsg:2056")

geo_df_bound = gpd.GeoDataFrame(geometry=[poly], crs="epsg:2056")

geo_df = gpd.overlay(df1=geo_df, df2=geo_df_bound, how="intersection")

geo_df["zsname"] = df_mean["zsname"]

geo_df = geo_df.to_crs(4326)

geo_p_df = (
    df[["lon", "lat"]]
    .apply(lambda x: shapely.geometry.Point(x.values[0], x.values[1]), axis=1)
    .reset_index()
)
geo_p_df.columns = ["index", "geometry"]

geo_p_df = geo_p_df.drop(columns="index")


def point_in(point):
    for j, poly in enumerate(geo_df["geometry"].values):
        if poly.contains(point):
            return geo_df["zsname"].values[j]
    return "Missing"

df["zsname"] = geo_p_df.apply(lambda x: point_in(x.values), axis=1)

In [50]:
# df_traffic["month"] = pd.to_datetime(df_traffic["messungdatzeit"]).dt.month
# df_traffic["day"] = pd.to_datetime(df_traffic["messungdatzeit"]).dt.day
# df_traffic["hour"] = pd.to_datetime(df_traffic["messungdatzeit"]).dt.hour

# agg_df = (
#     df_traffic.groupby(["zsname", "month", "day", "hour"])["anzfahrzeuge"]
#     .sum()
#     .reset_index()
# )

# agg_df["prob"] = agg_df["anzfahrzeuge"] / agg_df.groupby(["month", "day", "hour"])[
#     "anzfahrzeuge"
# ].transform("sum")

agg_df = df_traffic.copy()

agg_df["score"] = (df_traffic["anzfahrzeuge"] / df_traffic["anzfahrzeuge"].sum())

agg_df["score"] = (1 / agg_df["score"]) / sum(1 / agg_df["score"])

tot_df = df.merge(agg_df, how="inner", on="zsname")

In [51]:
fig = go.Figure()

grouped=tot_df.groupby("score")

for name, group in grouped:
    fig.add_scattermapbox(
        lat=group["lat"], 
        lon=group["lon"], 
        mode="markers"
    )

fig.update_layout(
    mapbox_style="stamen-toner",
    mapbox_zoom=11,
    mapbox_center={"lon": 8.540327377790328, "lat": 47.37792336422763},
    height=600,
    width=900,
)

fig.show()

In [54]:
import plotly.express as px

plot_df = tot_df[tot_df["score"] != max(tot_df["score"])]

fig=px.scatter_mapbox(plot_df, lat="lat", lon="lon", color="score")

fig.update_layout(
    mapbox_style="stamen-toner",
    mapbox_zoom=11,
    mapbox_center={"lon": 8.540327377790328, "lat": 47.37792336422763},
    height=600,
    width=900,
)
fig.show()